# Data cleansing and formatting
## Truncate into windows 
## Pad with same window length

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from sklearn import preprocessing

df_acquiring = pd.read_csv('./df_acquiring.csv')
df_acquired = pd.read_csv('./df_acquired.csv')
df_funding = pd.read_csv('./df_funding.csv')
df_ipo = pd.read_csv('./df_ipo.csv')
df_milestone = pd.read_csv("sentimented_milestone.csv")
df_product = pd.read_csv("cleaned_product.csv")

df = pd.read_csv("sample-results.csv")
df_acquired["acquired_time_since_founded"] = df_acquired["acquired_time_since_founded"].apply(
    lambda x : int(x[1:-2]))
df_acquiring["acquiring_time_since_founded"] = df_acquiring["acquiring_time_since_founded"].apply(
    lambda x : int(x[1:-2]))
df_ipo["time_since_founded"] = df_ipo["time_since_founded"].apply(
    lambda x : int(x[1:-1]))
pd.options.display.max_columns = None


In [109]:
window_size = 180

In [25]:
#Helper function
def printnan(df):
    null_columns = df.columns[df.isnull().any()]
    print(df[null_columns].isnull().sum())

In [99]:
df_product = pd.read_csv("cleaned_product.csv")
df_product.drop(columns=['id','founded_at','status', 'normalized_name', 'company_found_at'],inplace=True)
df_product.rename(columns={"since_founded": "product_time_since_founded","parent_id":"product_object_id"},inplace=True)
df_product = df_product[df_product['product_time_since_founded'].gt(-0.1)]

display(df_product.columns)


Index(['product_object_id', 'product_time_since_founded', 'alpha', 'beta',
       'closed', 'development', 'live', 'operating', 'private'],
      dtype='object')

In [100]:
def normalize(x):
    x = x.values.reshape(-1, 1)
    min_max_scaler = preprocessing.MinMaxScaler()
    x_scaled = min_max_scaler.fit_transform(x)
    return x_scaled

df_acquiring["price_amount"] = pd.DataFrame(normalize(df_acquiring["price_amount"]))
groups =  df_funding.groupby("funding_round_code")["raised_amount_usd"]
for name, group in groups:
    a = normalize(group)
    df_funding.at[group.index,"raised_amount_usd"] = normalize(group)


In [101]:
df_funding.drop(columns=['Unnamed: 0','funding_round_code','participants'],inplace=True)
df_funding.rename(columns={"time_since_founded": "funding_time_since_founded","object_id":"funding_object_id"},inplace=True)

df_milestone.drop(columns=['Unnamed: 0', 'Unnamed: 0.1','milestone_at', 'description', 'embedding', 'company_found_at'],inplace=True)
df_milestone.rename(columns={"since_founded": "milstone_time_since_founded","object_id":"milestone_object_id"},inplace=True)


df_ipo.drop(columns='Unnamed: 0',inplace=True)
df_ipo.rename(columns={"time_since_founded":"ipo_time_since_founded"},inplace=True)
df_acquiring.drop(columns='acquired_object_id',inplace=True)


df_acquired=df_acquired.loc[:,['acquired_object_id','acquired_time_since_founded']]

# Merge fundings

In [118]:
allcolumns = ["funding_object_id"]
for i in range(186):
    allcolumns += ['window' + str(i)]
for i in range(1,186):
    allcolumns += ['funding_window' + str(i)]
allcolumns
df_unique = pd.DataFrame(columns=allcolumns)
df_unique["funding_object_id"] = df_funding.drop_duplicates("funding_object_id")["funding_object_id"]

def mergeFunding(x):
    row = []
    df_row = df_funding.loc[df_funding["funding_object_id"] == x["funding_object_id"]]
    print(x["funding_object_id"])
    max_time = df_row["funding_time_since_founded"].max()
    for i in range(int(max_time/window_size)+1):
        #print(df_funding.loc[df_funding["funding_object_id"] == x["funding_object_id"]])

        item = df_row.loc[(df_row["funding_time_since_founded"] >= i * window_size)
                          & (df_row["funding_time_since_founded"] < (i+1) * window_size)]
        row.append(item.iloc[:,1:10].sum().values)
    for i in range(int(max_time/window_size)+1, 186):
        row.append(np.nan)
    return list(row)

df_unique.iloc[:,1:187] = df_unique.apply(mergeFunding, axis=1,result_type='expand').values

c:144040
c:18038
c:161452
c:161453
c:161480
c:264245
c:18202
c:51578
c:161699
c:161944
c:4299
c:263989
c:68549
c:68486
c:68442
c:162067
c:18701
c:18741
c:264553
c:68329
c:45196
c:69063
c:265497
c:161240
c:265463
c:64996
c:17758
c:265370
c:69596
c:265241
c:161312
c:161360
c:17842
c:69451
c:69368
c:17901
c:17908
c:17957
c:17966
c:161406
c:162175
c:68264
c:18865
c:162540
c:263402
c:42053
c:19825
c:19844
c:263275
c:67570
c:67375
c:162684
c:263065
c:67300
c:67272
c:67240
c:161102
c:67159
c:66912
c:255275
c:19707
c:19687
c:19628
c:19586
c:162223
c:18941
c:192650
c:18996
c:162275
c:68048
c:19044
c:19104
c:161236
c:19141
c:19244
c:67905
c:18731
c:19434
c:19462
c:67860
c:19526
c:19562
c:19153
c:65718
c:69710
c:69790
c:15669
c:15671
c:268100
c:268099
c:72413
c:72344
c:72295
c:159858
c:267584
c:16158
c:16177
c:16178
c:267295
c:16344
c:226874
c:71635
c:267124
c:34545
c:71582
c:159327
c:159219
c:15129
c:70893
c:15199
c:15257
c:73299
c:15407
c:268447
c:268492
c:268470
c:151530
c:15463
c:72914
c:7275

c:57891
c:173030
c:173052
c:173253
c:9841
c:57738
c:57721
c:173501
c:173610
c:29878
c:57588
c:173735
c:69583
c:218980
c:172497
c:42553
c:57964
c:57992
c:60709
c:58255
c:171470
c:171553
c:59243
c:58136
c:171848
c:28367
c:240616
c:27300
c:154430
c:172028
c:172030
c:171134
c:167615
c:28805
c:172199
c:172313
c:239377
c:57311
c:57308
c:30688
c:155670
c:174147
c:30709
c:30717
c:30728
c:56956
c:56904
c:30880
c:56861
c:137901
c:30984
c:31001
c:31031
c:31048
c:31083
c:31087
c:30670
c:57085
c:57091
c:57112
c:173915
c:173942
c:30202
c:173980
c:57275
c:57272
c:153911
c:57252
c:28022
c:57237
c:238987
c:229383
c:815
c:238967
c:189232
c:177503
c:30620
c:30623
c:53065
c:508
c:171449
c:27901
c:246154
c:168399
c:245862
c:59643
c:168574
c:245588
c:230964
c:226588
c:168801
c:168821
c:168975
c:59456
c:59420
c:169118
c:182691
c:244730
c:59286
c:168362
c:246241
c:168315
c:59857
c:247388
c:167427
c:167517
c:88478
c:25076
c:247214
c:60301
c:167540
c:58795
c:163400
c:246958
c:167932
c:246596
c:246582
c:25306
c:

c:58527
c:83037
c:1021
c:19948
c:190225
c:241840
c:238570
c:69953
c:75469
c:152855
c:173835
c:96669
c:163104
c:19895
c:175620
c:48698
c:59625
c:103561
c:155241
c:67432
c:173983
c:183915
c:169433
c:181345
c:265442
c:57264
c:285278
c:255295
c:285107
c:30605
c:78214
c:285830
c:171600
c:140462
c:269034
c:70468
c:257152
c:231273
c:224266
c:32377
c:155039
c:4421
c:67965
c:268970
c:19154
c:213816
c:82519
c:20836
c:43790
c:1414
c:105893
c:1909
c:277934
c:44
c:151809
c:40089
c:278308
c:280061
c:155371
c:8199
c:183280
c:221183
c:146899
c:77780
c:137042
c:454
c:271290
c:270443
c:76789
c:26669
c:237831
c:126
c:182822
c:177466
c:177461
c:178205
c:68559
c:1415
c:157
c:20677
c:34085
c:44794
c:135035
c:34338
c:78877
c:179393
c:161447
c:142364
c:34335
c:151231
c:213107
c:24105
c:9673
c:170036
c:210280
c:178203
c:156172
c:193827
c:69343
c:235718
c:5353
c:166904
c:280898
c:6011
c:2221
c:101312
c:53847
c:180599
c:55661
c:320
c:77201
c:2478
c:41062
c:145518
c:706
c:164754
c:140139
c:63621
c:280
c:167772
c:

c:86134
c:209829
c:835
c:175731
c:77678
c:253
c:247511
c:33507
c:28718
c:193873
c:52052
c:185001
c:72486
c:193054
c:54787
c:3242
c:33127
c:185462
c:11521
c:201730
c:238938
c:20384
c:272827
c:261639
c:49176
c:271579
c:3110
c:1352
c:74703
c:24973
c:82678
c:152060
c:186836
c:285
c:190207
c:47555
c:22437
c:160620
c:32934
c:233148
c:185821
c:174288
c:167620
c:67285
c:165211
c:152500
c:185400
c:49031
c:151618
c:110372
c:171454
c:252118
c:4419
c:245514
c:29218
c:36069
c:162865
c:264815
c:34269
c:166979
c:78336
c:24000
c:157893
c:162938
c:9611
c:118573
c:63217
c:15599
c:41316
c:166463
c:239196
c:172077
c:145113
c:234882
c:260831
c:59017
c:170625
c:268769
c:101317
c:169483
c:211308
c:178509
c:51932
c:235697
c:182445
c:68444
c:1721
c:8128
c:84
c:176224
c:46811
c:166899
c:167786
c:24892
c:202538
c:52921
c:67568
c:139334
c:3417
c:53997
c:135515
c:71371
c:18740
c:233060
c:144928
c:37145
c:67394
c:259051
c:45689
c:166173
c:154052
c:139570
c:267271
c:146488
c:42378
c:1902
c:10923
c:291
c:1634
c:19208

c:210735
c:202795
c:272028
c:20534
c:188054
c:160027
c:13923
c:10252
c:31160
c:159498
c:163
c:176262
c:20251
c:187463
c:75408
c:61666
c:65867
c:204993
c:23347
c:166956
c:57001
c:156584
c:195345
c:186041
c:138141
c:156709
c:38780
c:240698
c:222474
c:237086
c:36759
c:43063
c:1177
c:237099
c:16807
c:168203
c:18465
c:40872
c:200216
c:139675
c:50890
c:58680
c:363
c:28746
c:720
c:206969
c:44418
c:29778
c:106304
c:159670
c:78008
c:90
c:240424
c:9740
c:192492
c:46835
c:1038
c:256271
c:72368
c:83757
c:148896
c:4730
c:1102
c:159241
c:9106
c:267817
c:218998
c:10180
c:73418
c:63507
c:18470
c:163454
c:5410
c:281557
c:3840
c:275469
c:55307
c:16145
c:66605
c:49816
c:18675
c:20487
c:200
c:156286
c:265302
c:1592
c:14486
c:164681
c:53248
c:12140
c:53275
c:58653
c:12272
c:72188
c:210415
c:14649
c:221995
c:257018
c:27545
c:2483
c:3205
c:225921
c:221989
c:222556
c:224342
c:152111
c:154249
c:269648
c:8957
c:39944
c:222387
c:191852
c:261017
c:33227
c:160604
c:219480
c:68337
c:3634
c:199649
c:50528
c:36192
c:

...

c:28573
c:18029
c:123
c:3779
c:1598
c:43589
c:6314
c:19101
c:142211
c:15769
c:15878
c:75308
c:34591
c:31827
c:66811
c:188695
c:56302
c:30254
c:5134
c:73
c:143761
c:29374
c:1445
c:31794
c:38235
c:31937
c:261214
c:141146
c:164526
c:268708
c:141367
c:42539
c:58170
c:39652
c:14844
c:77925
c:48619
c:74382
c:27879
c:23095
c:13924
c:74911
c:35603
c:50734
c:5532
c:1673
c:20059
c:11574
c:279004
c:10643
c:218599
c:160972
c:83437
c:33383
c:177750
c:140615
c:279001
c:70239
c:279513
c:3000
c:58823
c:86219
c:3394
c:177771
c:22570
c:1749
c:167361
c:61894
c:160052
c:218503
c:85761
c:58226
c:155758
c:86077
c:15135
c:36781
c:11429
c:177994
c:280770
c:15952
c:82574
c:171994
c:66539
c:142553
c:95330
c:36004
c:43696
c:32615
c:281337
c:235921
c:281425
c:164533
c:71088
c:60545
c:61790
c:85167
c:235621
c:36316
c:28108
c:270895
c:47350
c:34736
c:30365
c:27755
c:3179
c:282707
c:25418
c:240329
c:186511
c:15833
c:70751
c:62669
c:1385
c:156652
c:25187
c:143468
c:156735
c:14375
c:179240
c:17620
c:40742
c:357
c:3674

c:3679
c:165977
c:169567
c:44305
c:259111
c:169564
c:31452
c:224075
c:36688
c:57880
c:242435
c:49448
c:64277
c:42932
c:55776
c:89051
c:29965
c:21856
c:265548
c:55702
c:146188
c:26236
c:15867
c:2182
c:158808
c:15817
c:21497
c:36584
c:37933
c:130176
c:101535
c:237735
c:41954
c:7376
c:8159
c:28554
c:32738
c:32215
c:42681
c:17923
c:218110
c:166156
c:173568
c:17056
c:35475
c:103903
c:139479
c:19483
c:17672
c:260839
c:263273
c:25844
c:56616
c:56669
c:56732
c:58695
c:40629
c:105305
c:37871
c:13645
c:25447
c:20843
c:48951
c:32011
c:265428
c:164041
c:44332
c:265623
c:266613
c:7009
c:80487
c:21394
c:34014
c:79221
c:242484
c:240876
c:39725
c:27883
c:60723
c:62543
c:57167
c:54066
c:31909
c:268418
c:25583
c:55642
c:11362
c:71845
c:143635
c:154327
c:53681
c:173032
c:47913
c:44237
c:75051
c:57653
c:20140
c:119778
c:46943
c:122638
c:50526
c:28299
c:237661
c:268610
c:227340
c:23963
c:21494
c:1254
c:30249
c:46368
c:214391
c:1404
c:35936
c:15383
c:26782
c:173269
c:643
c:27021
c:17801
c:55354
c:59288
c:13

c:175535
c:24827
c:19023
c:58599
c:58345
c:34602
c:42737
c:275581
c:175982
c:20205
c:44733
c:21501
c:1663
c:37872
c:59118
c:1820
c:13262
c:35725
c:50925
c:140638
c:1418
c:25107
c:24545
c:50055
c:55089
c:154057
c:37248
c:45525
c:30667
c:58368
c:152388
c:20678
c:276705
c:24161
c:277512
c:27274
c:268719
c:3182
c:25033
c:12285
c:234793
c:49406
c:54008
c:170899
c:36292
c:9668
c:257063
c:61369
c:47512
c:35761
c:177752
c:44011
c:265853
c:30612
c:52015
c:38058
c:3805
c:6746
c:40200
c:71639
c:281062
c:41550
c:36289
c:167539
c:36290
c:41434
c:16405
c:268661
c:56554
c:36615
c:16224
c:1616
c:490
c:1715
c:6761
c:37925
c:265104
c:3600
c:6386
c:35756
c:20747
c:12885
c:2909
c:143495
c:68995
c:50872
c:56568
c:22295
c:72882
c:15976
c:235298
c:258980
c:222836
c:40664
c:245076
c:45849
c:29746
c:17521
c:33415
c:63926
c:37773
c:36579
c:58091
c:268590
c:38154
c:34059
c:35562
c:41248
c:145694
c:39060
c:59675
c:21312
c:34680
c:83845
c:236591
c:281559
c:28333
c:47524
c:227481
c:15120
c:9458
c:2507
c:1266
c:5837

c:457
c:8533
c:27440
c:19006
c:74175
c:235581
c:8037
c:226916
c:3194
c:43337
c:13016
c:31257
c:52543
c:42384
c:12906
c:244291
c:82786
c:17282
c:8358
c:58865
c:36928
c:52572
c:43483
c:46267
c:83305
c:9390
c:18027
c:43525
c:60544
c:46041
c:25489
c:46676
c:49421
c:207986
c:42610
c:57893
c:60407
c:42158
c:45539
c:247147
c:247600
c:13464
c:6451
c:67015
c:17275
c:194030
c:195038
c:48700
c:48708
c:8017
c:55138
c:39058
c:34053
c:260050
c:138810
c:27429
c:23076
c:24995
c:236683
c:28832
c:268339
c:24635
c:42698
c:42605
c:167125
c:32044
c:261067
c:265265
c:9614
c:38589
c:57124
c:4582
c:45434
c:26243
c:247017
c:11507
c:268886
c:49439
c:172912
c:38469
c:31936
c:3405
c:8453
c:206616
c:14009
c:34645
c:175766
c:273843
c:58583
c:247524
c:80800
c:44326
c:267237
c:59041
c:223233
c:9663
c:31873
c:235044
c:11976
c:174092
c:31664
c:33864
c:60593
c:22028
c:17656
c:266926
c:18135
c:65847
c:59924
c:273812
c:82918
c:59147
c:66395
c:57157
c:171047
c:45869
c:34655
c:16488
c:34651
c:19861
c:64561
c:7331
c:266157
c

c:44544
c:24716
c:40281
c:2294
c:68336
c:37838
c:25217
c:46165
c:25852
c:198650
c:80940
c:49117
c:7199
c:245016
c:38965
c:20395
c:13204
c:8004
c:20178
c:71232
c:27967
c:33592
c:136363
c:193658
c:36587
c:40870
c:25141
c:25556
c:20547
c:40017
c:1245
c:74253
c:49566
c:59551
c:5187
c:47275
c:25137
c:33609
c:11901
c:24719
c:58712
c:25534
c:59966
c:69622
c:210293
c:214652
c:51503
c:10132
c:19700
c:160079
c:236510
c:44681
c:150080
c:57892
c:40268
c:48371
c:38578
c:195923
c:3982
c:45730
c:25507
c:216792
c:231609
c:171426
c:84020
c:43608
c:238717
c:7994
c:46831
c:245916
c:43601
c:51954
c:158045
c:74313
c:43874
c:201169
c:243321
c:37350
c:30229
c:83135
c:17273
c:17076
c:26156
c:234001
c:26418
c:28424
c:7554
c:1433
c:44436
c:2254
c:15631
c:170452
c:184737
c:36229
c:60185
c:267764
c:27939
c:268821
c:36317
c:73886
c:81543
c:244289
c:270215
c:182945
c:37240
c:59736
c:27748
c:275462
c:236888
c:13519
c:40254
c:266129
c:236240
c:38655
c:36059
c:41093
c:25997
c:143228
c:46297
c:22988
c:2623
c:58862
c:24

In [121]:
def fundingY(x):
    print(x["funding_object_id"])
    for i in range(2,187):
        if (np.array_equal(x.iloc[i], np.zeros(9)) == False)& (np.isnan(x.iloc[i]).all() == False):
            x.iloc[185+i] =1
        else:
            x.iloc[185+i] =0
    return x
        
df_unique = df_unique.apply(fundingY,axis=1)

c:144040
c:144040
c:18038
c:161452
c:161453
c:161480
c:264245
c:18202
c:51578
c:161699
c:161944
c:4299
c:263989
c:68549
c:68486
c:68442
c:162067
c:18701
c:18741
c:264553
c:68329
c:45196
c:69063
c:265497
c:161240
c:265463
c:64996
c:17758
c:265370
c:69596
c:265241
c:161312
c:161360
c:17842
c:69451
c:69368
c:17901
c:17908
c:17957
c:17966
c:161406
c:162175
c:68264
c:18865
c:162540
c:263402
c:42053
c:19825
c:19844
c:263275
c:67570
c:67375
c:162684
c:263065
c:67300
c:67272
c:67240
c:161102
c:67159
c:66912
c:255275
c:19707
c:19687
c:19628
c:19586
c:162223
c:18941
c:192650
c:18996
c:162275
c:68048
c:19044
c:19104
c:161236
c:19141
c:19244
c:67905
c:18731
c:19434
c:19462
c:67860
c:19526
c:19562
c:19153
c:65718
c:69710
c:69790
c:15669
c:15671
c:268100
c:268099
c:72413
c:72344
c:72295
c:159858
c:267584
c:16158
c:16177
c:16178
c:267295
c:16344
c:226874
c:71635
c:267124
c:34545
c:71582
c:159327
c:159219
c:15129
c:70893
c:15199
c:15257
c:73299
c:15407
c:268447
c:268492
c:268470
c:151530
c:15463
c:729

c:190631
c:190579
c:211180
c:42769
c:176689
c:210891
c:42819
c:42826
c:181064
c:471
c:189562
c:23991
c:42931
c:190290
c:42976
c:181932
c:190478
c:209913
c:209912
c:43114
c:51775
c:36869
c:36157
c:172664
c:172767
c:172794
c:57891
c:173030
c:173052
c:173253
c:9841
c:57738
c:57721
c:173501
c:173610
c:29878
c:57588
c:173735
c:69583
c:218980
c:172497
c:42553
c:57964
c:57992
c:60709
c:58255
c:171470
c:171553
c:59243
c:58136
c:171848
c:28367
c:240616
c:27300
c:154430
c:172028
c:172030
c:171134
c:167615
c:28805
c:172199
c:172313
c:239377
c:57311
c:57308
c:30688
c:155670
c:174147
c:30709
c:30717
c:30728
c:56956
c:56904
c:30880
c:56861
c:137901
c:30984
c:31001
c:31031
c:31048
c:31083
c:31087
c:30670
c:57085
c:57091
c:57112
c:173915
c:173942
c:30202
c:173980
c:57275
c:57272
c:153911
c:57252
c:28022
c:57237
c:238987
c:229383
c:815
c:238967
c:189232
c:177503
c:30620
c:30623
c:53065
c:508
c:171449
c:27901
c:246154
c:168399
c:245862
c:59643
c:168574
c:245588
c:230964
c:226588
c:168801
c:168821
c:1689

c:275723
c:31159
c:24727
c:83034
c:32749
c:22449
c:75778
c:33737
c:141876
c:2160
c:163987
c:59009
c:33231
c:265759
c:78821
c:159900
c:67160
c:12592
c:60940
c:29150
c:193605
c:236055
c:59710
c:156772
c:18537
c:193618
c:215653
c:234586
c:153296
c:71674
c:76324
c:234195
c:1222
c:23764
c:153666
c:191081
c:21523
c:60930
c:53677
c:187555
c:23958
c:193182
c:58527
c:83037
c:1021
c:19948
c:190225
c:241840
c:238570
c:69953
c:75469
c:152855
c:173835
c:96669
c:163104
c:19895
c:175620
c:48698
c:59625
c:103561
c:155241
c:67432
c:173983
c:183915
c:169433
c:181345
c:265442
c:57264
c:285278
c:255295
c:285107
c:30605
c:78214
c:285830
c:171600
c:140462
c:269034
c:70468
c:257152
c:231273
c:224266
c:32377
c:155039
c:4421
c:67965
c:268970
c:19154
c:213816
c:82519
c:20836
c:43790
c:1414
c:105893
c:1909
c:277934
c:44
c:151809
c:40089
c:278308
c:280061
c:155371
c:8199
c:183280
c:221183
c:146899
c:77780
c:137042
c:454
c:271290
c:270443
c:76789
c:26669
c:237831
c:126
c:182822
c:177466
c:177461
c:178205
c:68559
c

c:41567
c:268966
c:71891
c:153019
c:180722
c:140734
c:229707
c:35620
c:22986
c:21915
c:273859
c:168572
c:83588
c:7837
c:202215
c:226452
c:68086
c:6627
c:53925
c:44847
c:70220
c:1637
c:243322
c:58944
c:193641
c:48759
c:268207
c:5320
c:273131
c:44149
c:48612
c:74017
c:65050
c:83397
c:167993
c:273427
c:257727
c:69089
c:68605
c:42955
c:199008
c:159558
c:84807
c:44980
c:264554
c:60970
c:148756
c:283084
c:25859
c:154329
c:75520
c:726
c:58291
c:160717
c:59408
c:177
c:273985
c:4584
c:86134
c:209829
c:835
c:175731
c:77678
c:253
c:247511
c:33507
c:28718
c:193873
c:52052
c:185001
c:72486
c:193054
c:54787
c:3242
c:33127
c:185462
c:11521
c:201730
c:238938
c:20384
c:272827
c:261639
c:49176
c:271579
c:3110
c:1352
c:74703
c:24973
c:82678
c:152060
c:186836
c:285
c:190207
c:47555
c:22437
c:160620
c:32934
c:233148
c:185821
c:174288
c:167620
c:67285
c:165211
c:152500
c:185400
c:49031
c:151618
c:110372
c:171454
c:252118
c:4419
c:245514
c:29218
c:36069
c:162865
c:264815
c:34269
c:166979
c:78336
c:24000
c:15

c:2497
c:192
c:30759
c:69283
c:202149
c:69291
c:1330
c:167734
c:22
c:258093
c:3134
c:65723
c:33711
c:77980
c:193110
c:41900
c:70667
c:58597
c:143173
c:87650
c:225798
c:79361
c:158255
c:27482
c:233641
c:243145
c:51877
c:169673
c:187260
c:16067
c:53759
c:160206
c:6454
c:82549
c:213124
c:82895
c:224872
c:70222
c:5301
c:30939
c:209962
c:1784
c:191941
c:719
c:85019
c:74692
c:74614
c:9608
c:159494
c:15229
c:195726
c:261146
c:221266
c:183217
c:161311
c:152332
c:1145
c:263219
c:164361
c:181791
c:162721
c:84518
c:8562
c:18082
c:169940
c:256343
c:83048
c:203956
c:166690
c:42416
c:145308
c:146643
c:166631
c:103388
c:210735
c:202795
c:272028
c:20534
c:188054
c:160027
c:13923
c:10252
c:31160
c:159498
c:163
c:176262
c:20251
c:187463
c:75408
c:61666
c:65867
c:204993
c:23347
c:166956
c:57001
c:156584
c:195345
c:186041
c:138141
c:156709
c:38780
c:240698
c:222474
c:237086
c:36759
c:43063
c:1177
c:237099
c:16807
c:168203
c:18465
c:40872
c:200216
c:139675
c:50890
c:58680
c:363
c:28746
c:720
c:206969
c:444

...

c:34199
c:198658
c:3980
c:78
c:48264
c:43345
c:1853
c:15072
c:30016
c:195657
c:6048
c:13049
c:176316
c:13059
c:131487
c:43048
c:60314
c:236631
c:173274
c:72062
c:160833
c:267760
c:77407
c:49247
c:44693
c:17405
c:86162
c:36689
c:267021
c:40372
c:24447
c:208198
c:165590
c:171497
c:9260
c:171267
c:61185
c:33411
c:270244
c:70843
c:269642
c:66211
c:86440
c:73155
c:236349
c:270815
c:16276
c:45365
c:169231
c:24393
c:45268
c:223783
c:25872
c:138056
c:35157
c:9924
c:176057
c:281161
c:58078
c:27472
c:18812
c:273965
c:81563
c:70564
c:40435
c:6410
c:67191
c:44734
c:179224
c:819
c:138904
c:12630
c:139042
c:3007
c:46329
c:66436
c:266739
c:268859
c:27397
c:9659
c:412
c:60577
c:168726
c:44917
c:30695
c:47842
c:225410
c:272442
c:61245
c:251666
c:266717
c:273924
c:175986
c:142795
c:58908
c:228332
c:793
c:207625
c:12790
c:19536
c:60361
c:31736
c:60243
c:34396
c:77478
c:38870
c:17725
c:265950
c:12352
c:261953
c:1258
c:102783
c:195501
c:106
c:20066
c:18730
c:27739
c:135326
c:236610
c:1203
c:153668
c:25098


c:27438
c:231621
c:79412
c:74877
c:51673
c:81560
c:51848
c:76876
c:55337
c:150135
c:32792
c:57600
c:236257
c:169421
c:236788
c:228644
c:49091
c:26183
c:237570
c:150843
c:51653
c:49822
c:61
c:272418
c:164970
c:68945
c:23439
c:24638
c:13729
c:3181
c:82540
c:46264
c:61226
c:25430
c:41923
c:179871
c:60458
c:36971
c:80763
c:220286
c:52406
c:17646
c:184890
c:27897
c:56503
c:28754
c:46411
c:144468
c:94897
c:8629
c:43950
c:169721
c:2955
c:3891
c:43752
c:18356
c:166380
c:6522
c:74352
c:45639
c:3195
c:270359
c:30343
c:27969
c:240399
c:69482
c:132127
c:243
c:173177
c:59708
c:27694
c:145452
c:66413
c:271211
c:30517
c:14746
c:20825
c:1043
c:80337
c:165
c:245201
c:169598
c:29369
c:211583
c:64484
c:245969
c:23542
c:53814
c:11514
c:23072
c:28398
c:36485
c:60489
c:39079
c:1538
c:191878
c:23915
c:12171
c:139933
c:9536
c:242603
c:246912
c:55320
c:31081
c:54295
c:37982
c:57507
c:28132
c:2235
c:168267
c:237847
c:255962
c:16582
c:155729
c:12308
c:39871
c:13174
c:21009
c:168527
c:143092
c:256415
c:219492
c:9

c:19862
c:47966
c:146291
c:13552
c:269494
c:73493
c:55088
c:241257
c:63460
c:24860
c:25339
c:259198
c:32411
c:35175
c:12543
c:59525
c:71754
c:68230
c:5306
c:89044
c:15645
c:949
c:3288
c:30987
c:15538
c:254211
c:72352
c:10583
c:56419
c:16402
c:268904
c:268897
c:268894
c:30604
c:7666
c:14903
c:170827
c:4018
c:4633
c:24132
c:4883
c:27650
c:37140
c:46062
c:23961
c:171123
c:58601
c:75516
c:237772
c:12957
c:28004
c:32061
c:56946
c:105414
c:32287
c:272616
c:265475
c:265557
c:140564
c:64503
c:69390
c:46190
c:22850
c:145352
c:264298
c:108085
c:268405
c:48315
c:16047
c:57835
c:268410
c:172526
c:63281
c:172698
c:269450
c:36936
c:56137
c:219016
c:33842
c:57828
c:61296
c:25801
c:36310
c:84798
c:43186
c:122643
c:27641
c:9655
c:34198
c:1525
c:68615
c:11821
c:172252
c:41303
c:33420
c:11888
c:7859
c:40972
c:122830
c:8523
c:13478
c:53955
c:9897
c:277331
c:272729
c:218708
c:27483
c:11394
c:45915
c:16277
c:38079
c:30477
c:20554
c:60022
c:47596
c:7900
c:59296
c:76153
c:272610
c:273113
c:56076
c:20378
c:356

c:194027
c:46693
c:44073
c:38843
c:6263
c:47689
c:43031
c:17818
c:45345
c:47841
c:159201
c:24147
c:46491
c:714
c:45691
c:149379
c:45797
c:155566
c:42555
c:47846
c:58494
c:31559
c:35653
c:3101
c:532
c:45820
c:12952
c:30961
c:59613
c:45611
c:12068
c:26912
c:5108
c:60402
c:3626
c:8502
c:48943
c:22897
c:51316
c:217927
c:27922
c:47257
c:27701
c:203151
c:285758
c:763
c:211313
c:45907
c:25544
c:17602
c:45610
c:36294
c:257482
c:44597
c:46629
c:30855
c:46799
c:11506
c:39223
c:15858
c:51568
c:43451
c:158546
c:20688
c:211442
c:9495
c:25140
c:58384
c:213357
c:271946
c:77603
c:51123
c:50601
c:51479
c:219230
c:31494
c:807
c:24372
c:27751
c:17829
c:33619
c:15552
c:51066
c:52527
c:46320
c:26140
c:237037
c:237121
c:48715
c:25900
c:19717
c:23384
c:18199
c:25404
c:24425
c:224617
c:224556
c:25379
c:3210
c:85240
c:46151
c:49906
c:49993
c:13741
c:227941
c:228702
c:1571
c:75834
c:228307
c:79645
c:231769
c:230450
c:25376
c:52466
c:17775
c:15165
c:26569
c:757
c:15832
c:189764
c:232218
c:231847
c:36650
c:33872


c:15834
c:27206
c:53255
c:23692
c:44113
c:44227
c:26572
c:213244
c:214597
c:32796
c:48618
c:231295
c:210296
c:151086
c:5378
c:9250
c:77968
c:43826
c:222583
c:225131
c:28434
c:4179
c:218174
c:25558
c:11600
c:21084
c:231044
c:12748
c:4726
c:42674
c:78918
c:829
c:19089
c:41270
c:26899
c:16875
c:186056
c:46371
c:164567
c:79332
c:46220
c:34397
c:14905
c:7277
c:34460
c:83306
c:270382
c:21933
c:422
c:265002
c:84869
c:14589
c:247320
c:255182
c:55051
c:268122
c:22190
c:169999
c:25411
c:260707
c:234035
c:45669
c:28110
c:52214
c:60248
c:5621
c:37631
c:31015
c:53684
c:43516
c:10967
c:38211
c:38363
c:29451
c:251246
c:18159
c:84581
c:8532
c:26158
c:32857
c:59394
c:11970
c:22284
c:51821
c:261013
c:268855
c:25052
c:60115
c:236962
c:51693
c:18345
c:85218
c:69375
c:12560
c:13084
c:141374
c:42796
c:177148
c:175176
c:46059
c:46767
c:265789
c:35947
c:20057
c:282702
c:85026
c:38498
c:14893
c:38608
c:58462
c:46243
c:57960
c:37074
c:41311
c:234839
c:181484
c:26019
c:46775
c:234426
c:17567
c:14993
c:16557
c:67

In [127]:
def fillzeros(x):
    #print(x)
    if np.isnan(x).all():
        x = np.zeros(9)
    return x

for i in range(1,187):
    df_unique.iloc[:,i] = df_unique.iloc[:,i].apply(fillzeros)

In [129]:
df_unique_funding = df_unique

In [130]:
for i in range(2,187):
    df_unique_funding.iloc[:,i] += df_unique_funding.iloc[:,i-1] 
df_unique_funding 

funding_object_id                                            window0  \
0              c:144040  [0.004440019733421037, 0.0, 0.0, 0.0, 0.0, 0.0...   
1               c:18038  [0.01958127793822479, 1.0, 0.0, 0.0, 0.0, 0.0,...   
2              c:161452  [0.0038446064932833143, 0.0, 0.0, 0.0, 0.0, 0....   
3              c:161453  [0.00044000195556424696, 0.0, 0.0, 0.0, 0.0, 0...   
4              c:161480  [0.012450622531126556, 0.0, 1.0, 0.0, 0.0, 0.0...   
5              c:264245  [0.04155704732096508, 0.0, 1.0, 0.0, 0.0, 0.0,...   
6               c:18202  [0.0018844528197903103, 0.0, 0.0, 0.0, 0.0, 0....   
7               c:51578  [0.034744237211860596, 0.0, 1.0, 0.0, 0.0, 0.0...   
8              c:161699  [0.002551122449433108, 0.0, 0.0, 0.0, 0.0, 0.0...   
9              c:161944  [0.04995249762488124, 0.0, 1.0, 0.0, 0.0, 0.0,...   
10               c:4299  [0.004440019733421037, 0.0, 0.0, 0.0, 0.0, 0.0...   
11             c:263989  [0.0028844572642545076, 0.0, 0.0, 0.0, 0.0, 0....   
12              c:68549  [0.00021777874568331416, 0.0, 0.0, 0.0, 0.0, 0...   
13              c:68486  [0.04155704732096508, 0.0, 1.0, 0.0, 0.0, 0.0,...   
14              c:68442  [0.0038446064932833143, 0.0, 0.0, 0.0, 0.0, 0....   
15             c:162067      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
16              c:18701  [0.00044000195556424696, 0.0, 0.0, 0.0, 0.0, 0...   
17              c:18741  [0.013936696834841741, 0.0, 1.0, 0.0, 0.0, 0.0...   
18             c:264553  [0.0011066715852070454, 0.0, 0.0, 0.0, 0.0, 0....   
19              c:68329  [0.024901245062253115, 0.0, 2.0, 0.0, 0.0, 0.0...   
20              c:45196  [0.0006317361410495157, 0.0, 0.0, 0.0, 0.0, 0....   
21              c:69063  [0.0038446064932833143, 0.0, 0.0, 0.0, 0.0, 0....   
22             c:265497  [0.0038446064932833143, 0.0, 0.0, 0.0, 0.0, 0....   
23             c:161240  [0.0066622518322303655, 0.0, 0.0, 0.0, 0.0, 0....   
24             c:265463  [0.00021777874568331416, 0.0, 0.0, 0.0, 0.0, 0...   
25              c:64996  [0.005106689363063835, 0.0, 0.0, 0.0, 0.0, 0.0...   
26              c:17758  [0.00586675062362926, 1.0, 0.0, 0.0, 0.0, 0.0,...   
27             c:265370  [0.00021777874568331416, 0.0, 0.0, 0.0, 0.0, 0...   
28              c:69596  [0.0008844483753261126, 0.0, 0.0, 0.0, 0.0, 0....   
29             c:265241  [0.0038446064932833143, 0.0, 0.0, 0.0, 0.0, 0....   
...                 ...                                                ...   
25821          c:261056      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25822          c:266200      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25824          c:145945      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25825           c:59556      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25826          c:220572      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25827          c:243852      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25828           c:69136      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25829          c:212776      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25830          c:244910      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25831           c:16243      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25832          c:277196      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25833            c:6713      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25834          c:245323      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25835           c:35691      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25836          c:219131      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25837          c:267819      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25838          c:177075      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25840          c:144811      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25841           c:36848      [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]   
25842          c:164565     

# Merge acquiring

In [142]:
allcolumns = ["acquiring_object_id"]
for i in range(226):
    allcolumns += ['acq' + str(i)]

df_unique_acquiring = pd.DataFrame(columns=allcolumns)
df_unique_acquiring ["acquiring_object_id"] = df_acquiring.drop_duplicates("acquiring_object_id")["acquiring_object_id"]
df_unique_acquiring.info()

def mergeAcquiring(x):
    row = []
    df_row = df_acquiring.loc[df_acquiring["acquiring_object_id"] == x["acquiring_object_id"]]
    #print(x["acquiring_object_id"])
    max_time = df_row["acquiring_time_since_founded"].max()
    for i in range(int(max_time/window_size)+1):
        item = df_row.loc[(df_row["acquiring_time_since_founded"] >= i * window_size)
                          & (df_row["acquiring_time_since_founded"] < (i+1) * window_size)]
        row.append(item.iloc[:,1:12].sum().values)
        #print(row)
    for i in range(int(max_time/window_size)+1, 226):
        row.append(np.nan)
    #print(len(row))
    return list(row)

df_unique_acquiring.iloc[:,1:227] = df_unique_acquiring.apply(mergeAcquiring, axis=1,result_type='expand').values

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2043 entries, 0 to 4129
Columns: 227 entries, acquiring_object_id to acq225
dtypes: object(227)
memory usage: 3.6+ MB


In [143]:
def fillzeros(x):
    #print(x)
    if np.isnan(x).all():
        x = np.zeros(11)
    return x

for i in range(1,227):
    df_unique_acquiring.iloc[:,i] = df_unique_acquiring.iloc[:,i].apply(fillzeros)

df_unique_acquiring
#df_unique.iloc[-1]

for i in range(2,227):
    df_unique_acquiring.iloc[:,i] += df_unique_acquiring.iloc[:,i-1] 
df_unique_acquiring

acquiring_object_id                                               acq0  \
0               c:260783  [0.00617047863247863, 0.0, 0.0, 0.0, 0.0, 0.0,...   
1                  c:307  [0.006138307692307692, 0.0, 0.0, 0.0, 0.0, 0.0...   
2                c:60326  [2.564102564102564e-05, 0.0, 0.0, 0.0, 0.0, 0....   
3                c:15461  [1.7948717948717948e-06, 0.0, 0.0, 0.0, 0.0, 0...   
4               c:192899  [8.461538461538462e-06, 0.0, 0.0, 0.0, 0.0, 0....   
5               c:138299  [3.8461538461538463e-07, 0.0, 0.0, 0.0, 0.0, 0...   
6                c:80259  [0.00617047863247863, 0.0, 0.0, 0.0, 0.0, 0.0,...   
7               c:166448  [0.005456826340326341, 0.0, 0.0, 0.0, 0.0, 0.0...   
8                c:82144  [0.008756655982905981, 0.0, 0.0, 0.0, 0.0, 0.0...   
9                 c:5457  [1.282051282051282e-07, 0.0, 0.0, 0.0, 0.0, 0....   
10               c:64703  [0.024862483910139642, 0.0, 0.0, 0.0, 0.0, 0.0...   
11              c:195859  [2.564102564102564e-06, 0.0, 0.0, 0.0, 0.0, 0....   
12              c:221698  [1.282051282051282e-07, 0.0, 0.0, 0.0, 0.0, 0....   
13              c:171432  [7.692307692307692e-08, 0.0, 0.0, 0.0, 0.0, 0....   
14               c:47470  [0.010414091337900964, 0.0, 0.0, 0.0, 0.0, 0.0...   
15               c:23010  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
16              c:279935  [0.00617047863247863, 0.0, 0.0, 0.0, 0.0, 0.0,...   
17               c:85143  [0.00617047863247863, 0.0, 0.0, 0.0, 0.0, 0.0,...   
18              c:207479  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
19               c:15180  [0.007766518783542041, 0.0, 0.0, 0.0, 0.0, 0.0...   
20              c:190559  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
21               c:84204  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
22               c:45891  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
23              c:175916  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
25              c:193054  [0.00617047863247863, 0.0, 0.0, 0.0, 0.0, 0.0,...   
26               c:45772  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
27              c:257213  [0.010414091337900964, 0.0, 0.0, 0.0, 0.0, 0.0...   
28              c:176998  [0.007553728370554177, 0.0, 0.0, 0.0, 0.0, 0.0...   
29              c:150328  [0.00617047863247863, 0.0, 0.0, 0.0, 0.0, 0.0,...   
30                c:9212  [1.282051282051282e-06, 0.0, 0.0, 1.0, 0.0, 0....   
...                  ...                                                ...   
4076             c:32510  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4077             c:59139  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4079            c:212202  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4081            c:284510  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4082              c:5580  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4085              c:3658  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4087            c:258527  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4090             c:26486  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4094             c:21683  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4097              c:7389  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4098             c:70194  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4100             c:83647  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4103              c:7060  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4104             c:31279  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4105              c:1246  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4106             c:20211  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4107             c:15446  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4108             c:59312  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4109             c:31357  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0

# Merge milestone

In [140]:
df_milestone = df_milestone[df_milestone['milstone_time_since_founded'].gt(-0.1)]

allcolumns = ["milestone_object_id"]
for i in range(223):
    allcolumns += ['mle' + str(i)]

df_unique_milestone = pd.DataFrame(columns=allcolumns)
df_unique_milestone ["milestone_object_id"] = df_milestone.drop_duplicates("milestone_object_id")["milestone_object_id"]
df_unique_milestone.info()

def mergeMilestone(x):
    row = []
    df_row = df_milestone.loc[df_milestone["milestone_object_id"] == x["milestone_object_id"]]
    print(x["milestone_object_id"])
    max_time = df_row["milstone_time_since_founded"].max()
    for i in range(int(max_time/window_size)+1):

        item = df_row.loc[(df_row["milstone_time_since_founded"] >= i * window_size)
                          & (df_row["milstone_time_since_founded"] < (i+1) * window_size)]
        row.append(item.iloc[:,2:6].sum().values)
    for i in range(int(max_time/window_size)+1, 223):
        row.append(np.nan)
    return list(row)

df_unique_milestone.iloc[:,1:224] = df_unique_milestone.apply(mergeMilestone, axis=1,result_type='expand').values

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8823 entries, 0 to 22921
Columns: 224 entries, milestone_object_id to mle222
dtypes: object(224)
memory usage: 15.1+ MB
c:12
c:59
c:314
c:283
c:6816
c:5874
c:2034
c:5085
c:1388
c:75
c:6947
c:3515
c:5411
c:2391
c:6501
c:4068
c:1972
c:5149
c:1298
c:97
c:6995
c:4366
c:7163
c:183
c:7199
c:3692
c:7127
c:1600
c:259
c:5067
c:766
c:7369
c:513
c:7367
c:607
c:7385
c:4235
c:178
c:5096
c:1127
c:60
c:1224
c:1094
c:5
c:1710
c:1863
c:132
c:200
c:2790
c:5469
c:2272
c:7571
c:1236
c:303
c:199
c:2709
c:494
c:463
c:3510
c:1001
c:4589
c:371
c:6340
c:465
c:290
c:3869
c:1669
c:6000
c:900
c:1165
c:1283
c:142
c:399
c:381
c:1238
c:261
c:3507
c:747
c:2004
c:7688
c:5867
c:4040
c:7299
c:2295
c:793
c:3555
c:1687
c:8249
c:479
c:8268
c:5272
c:8339
c:1613
c:8373
c:8408
c:658
c:241
c:130
c:444
c:2282
c:7790
c:8496
c:8494
c:6079
c:5696
c:46
c:228
c:8515
c:647
c:2859
c:67
c:7521
c:523
c:1812
c:8613
c:959
c:3405
c:8774
c:856
c:277
c:682
c:8941
c:5420
c:4802
c:8881
c:29
c:3

c:32667
c:38752
c:23
c:19744
c:45325
c:31601
c:23901
c:20459
c:36985
c:38050
c:30538
c:1038
c:28520
c:148
c:10857
c:5399
c:3978
c:3825
c:46008
c:45469
c:45990
c:41298
c:42507
c:45888
c:19669
c:44621
c:27839
c:3625
c:30037
c:24623
c:39865
c:5924
c:3670
c:15
c:35333
c:424
c:8523
c:2646
c:20303
c:1621
c:9175
c:18233
c:43063
c:37499
c:46555
c:45841
c:46553
c:34404
c:3600
c:2351
c:45906
c:33588
c:45016
c:39540
c:19923
c:39649
c:46671
c:22649
c:45936
c:46753
c:17757
c:46652
c:630
c:45492
c:20248
c:46798
c:24263
c:40294
c:12334
c:32700
c:14610
c:32706
c:22511
c:47062
c:22721
c:10702
c:46630
c:46354
c:32352
c:15607
c:46030
c:38473
c:5487
c:35663
c:32904
c:31508
c:16548
c:20676
c:47356
c:41238
c:2519
c:24719
c:34021
c:43240
c:38071
c:26691
c:2772
c:9939
c:5697
c:47528
c:122
c:11486
c:21391
c:20487
c:43274
c:20800
c:45950
c:43574
c:44075
c:35511
c:773
c:39297
c:47794
c:16933
c:47470
c:41825
c:44439
c:16592
c:41833
c:29273
c:45673
c:25152
c:158
c:1579
c:113
c:929
c:32878
c:47878
c:8885
c:48039
c:

c:41923
c:6165
c:25952
c:57339
c:58128
c:3409
c:43552
c:33859
c:7711
c:58837
c:57960
c:58875
c:58878
c:1242
c:15850
c:22916
c:58134
c:30607
c:58849
c:30343
c:33592
c:591
c:8972
c:16326
c:33873
c:28468
c:3455
c:58992
c:59003
c:53991
c:57412
c:10614
c:640
c:53464
c:49109
c:1673
c:30351
c:57941
c:44513
c:15008
c:24393
c:26023
c:59266
c:26977
c:24371
c:2277
c:18418
c:59177
c:58821
c:59362
c:3000
c:19920
c:25020
c:27980
c:13267
c:2345
c:36499
c:42282
c:19725
c:54136
c:28404
c:39953
c:25833
c:31615
c:32618
c:57624
c:13196
c:59476
c:44810
c:42296
c:59286
c:59638
c:22675
c:32383
c:27935
c:59283
c:55323
c:13249
c:59157
c:49255
c:17124
c:568
c:15975
c:27024
c:2789
c:20098
c:59772
c:15614
c:59779
c:59840
c:59677
c:17610
c:39965
c:40587
c:37345
c:33426
c:39320
c:21341
c:24508
c:53443
c:59762
c:33009
c:20430
c:56412
c:31482
c:44723
c:24444
c:25108
c:54324
c:18532
c:9050
c:4
c:39908
c:9130
c:47774
c:59800
c:352
c:23972
c:7879
c:50210
c:47996
c:60155
c:25567
c:25200
c:9195
c:38219
c:42127
c:57587
c:5

c:6670
c:59690
c:66538
c:70029
c:57795
c:70017
c:28553
c:72666
c:14239
c:35658
c:73521
c:73523
c:7570
c:65940
c:56149
c:42724
c:73494
c:73518
c:51546
c:15135
c:554
c:30685
c:20938
c:25836
c:13816
c:72842
c:73137
c:4468
c:11747
c:18145
c:43502
c:25375
c:45324
c:2226
c:28487
c:60000
c:25109
c:73504
c:30954
c:73898
c:50756
c:70205
c:24283
c:12623
c:71904
c:31005
c:48251
c:73458
c:64701
c:73981
c:73768
c:72982
c:38010
c:65515
c:18029
c:33987
c:25293
c:74102
c:74116
c:60623
c:62526
c:74114
c:54006
c:74141
c:29225
c:74265
c:73470
c:14904
c:73346
c:66729
c:24252
c:18478
c:14334
c:26135
c:71105
c:69595
c:69499
c:4020
c:74226
c:51852
c:28159
c:18401
c:29095
c:54823
c:68141
c:74319
c:4947
c:64171
c:34094
c:74609
c:62359
c:31228
c:37200
c:71344
c:31121
c:14949
c:1674
c:24215
c:25404
c:74573
c:74725
c:66446
c:74089
c:14760
c:41435
c:44929
c:74323
c:62198
c:74828
c:66890
c:20378
c:74394
c:74197
c:18275
c:14514
c:3168
c:53799
c:57514
c:64828
c:46956
c:68646
c:291
c:64902
c:57766
c:67306
c:85990
c:69

c:67092
c:46625
c:123016
c:105130
c:105413
c:136421
c:48944
c:88779
c:141404
c:139746
c:63402
c:136603
c:35331
c:31679
c:7653
c:142134
c:30804
c:44071
c:74583
c:75975
c:62136
c:84343
c:83752
c:142294
c:142268
c:141128
c:38799
c:141814
c:58497
c:141266
c:141593
c:62378
c:142023
c:142150
c:74279
c:86385
c:41593
c:1103
c:26211
c:142510
c:83141
c:17902
c:80559
c:131847
c:84017
c:46129
c:44235
c:16995
c:142713
c:12815
c:18056
c:104650
c:89605
c:75179
c:70955
c:65564
c:68575
c:62006
c:139929
c:84733
c:83641
c:142891
c:19066
c:23989
c:20606
c:64476
c:116050
c:81625
c:6558
c:21496
c:142181
c:44705
c:83721
c:66920
c:59054
c:11987
c:17548
c:80110
c:47064
c:51577
c:21595
c:62302
c:74877
c:78111
c:2921
c:71208
c:29818
c:77502
c:143565
c:53377
c:84758
c:1104
c:75461
c:56630
c:78458
c:104057
c:37396
c:143350
c:20267
c:63582
c:48068
c:141884
c:14642
c:78472
c:61244
c:10272
c:34408
c:131375
c:143745
c:79106
c:54933
c:46156
c:141860
c:50165
c:143959
c:64300
c:142552
c:37673
c:86063
c:12608
c:132471
c:5

c:160643
c:883
c:143560
c:4451
c:45395
c:158812
c:49937
c:3396
c:63027
c:147685
c:161627
c:161751
c:391
c:37849
c:141735
c:74825
c:49878
c:161653
c:145334
c:83993
c:17801
c:161931
c:161763
c:160795
c:162277
c:151618
c:161921
c:78564
c:26356
c:83279
c:155854
c:159829
c:85625
c:77454
c:84956
c:157033
c:56729
c:147665
c:142801
c:57810
c:74367
c:62821
c:85352
c:70121
c:162939
c:44164
c:159407
c:45757
c:159552
c:148904
c:160044
c:53885
c:156340
c:23418
c:36288
c:163147
c:162370
c:43337
c:160685
c:76019
c:161506
c:142292
c:143352
c:153254
c:162623
c:86328
c:56358
c:147754
c:156114
c:163185
c:63993
c:78106
c:151899
c:1230
c:695
c:163565
c:105642
c:22548
c:85137
c:163583
c:157815
c:160745
c:163150
c:52406
c:148687
c:155329
c:149089
c:157790
c:163153
c:163741
c:65439
c:66796
c:84389
c:152106
c:159674
c:146607
c:148225
c:157894
c:32375
c:47906
c:621
c:162093
c:30926
c:154117
c:159608
c:155371
c:159257
c:158780
c:163579
c:46622
c:153158
c:79261
c:164168
c:61896
c:54026
c:164212
c:84944
c:36061
c:

c:66695
c:154754
c:184587
c:176228
c:66444
c:69521
c:25558
c:184182
c:27726
c:180827
c:169564
c:178141
c:3824
c:10296
c:141841
c:183915
c:47121
c:184744
c:184890
c:83535
c:15034
c:13927
c:152670
c:148756
c:183697
c:46402
c:155335
c:184899
c:149062
c:44086
c:171751
c:184215
c:159841
c:158623
c:3596
c:178638
c:185313
c:185290
c:159840
c:185208
c:53214
c:139795
c:152348
c:37241
c:169626
c:75536
c:185255
c:179676
c:35341
c:179187
c:7979
c:73414
c:147242
c:155630
c:49315
c:177391
c:179941
c:53142
c:109713
c:158031
c:175972
c:185641
c:110383
c:77375
c:17455
c:39751
c:185816
c:33773
c:160192
c:185716
c:75681
c:186035
c:154240
c:182042
c:178738
c:160675
c:23588
c:25211
c:185109
c:181298
c:158238
c:10721
c:22219
c:170346
c:186433
c:736
c:60835
c:182908
c:12308
c:171993
c:185906
c:41005
c:27946
c:178962
c:176077
c:149682
c:181625
c:183920
c:76950
c:186345
c:145251
c:174617
c:186343
c:48543
c:177454
c:186542
c:157548
c:26681
c:186301
c:148492
c:79936
c:180938
c:175064
c:58343
c:186273
c:182597
c:

c:176782
c:207266
c:47622
c:105231
c:12273
c:6944
c:156719
c:176460
c:222909
c:75416
c:151312
c:51670
c:174872
c:196940
c:204709
c:225960
c:225962
c:176463
c:28959
c:157755
c:177215
c:24707
c:11552
c:222651
c:295
c:224436
c:36675
c:154884
c:162938
c:40145
c:170804
c:227207
c:226681
c:216603
c:40288
c:56163
c:157931
c:227278
c:199432
c:188244
c:227349
c:32944
c:19727
c:227206
c:182044
c:154123
c:182268
c:227342
c:134365
c:202834
c:220374
c:227843
c:228370
c:211060
c:65160
c:15815
c:77412
c:183652
c:183785
c:228282
c:228489
c:228236
c:17205
c:189668
c:52658
c:227348
c:193722
c:31518
c:80042
c:3044
c:228947
c:69634
c:217391
c:229300
c:17533
c:228821
c:228921
c:126117
c:19747
c:208284
c:182054
c:185457
c:28921
c:168122
c:219721
c:229277
c:224414
c:218403
c:206316
c:223442
c:208802
c:171910
c:79900
c:230642
c:225164
c:57216
c:23967
c:68470
c:26001
c:245095
c:158494
c:223902
c:219219
c:182716
c:170571
c:229919
c:230990
c:231125
c:230778
c:229850
c:231371
c:173229
c:4347
c:171981
c:26566
c:18

c:241876
c:85905
c:207249
c:267560
c:187441
c:165894
c:177720
c:266927
c:190534
c:56466
c:260351
c:69517
c:267737
c:76592
c:35787
c:267809
c:5580
c:55121
c:47823
c:49438
c:265583
c:1623
c:20116
c:203460
c:237021
c:267696
c:144385
c:235051
c:267689
c:151156
c:267465
c:75883
c:267655
c:218377
c:237446
c:267817
c:19948
c:268288
c:236271
c:267868
c:48124
c:268378
c:151939
c:267016
c:180030
c:267372
c:191077
c:268461
c:268556
c:234919
c:13330
c:268415
c:268476
c:221290
c:42598
c:268234
c:36004
c:263909
c:71848
c:138548
c:268927
c:813
c:82353
c:233233
c:268813
c:269025
c:267216
c:255336
c:269104
c:142176
c:268086
c:207186
c:266453
c:269034
c:174803
c:190508
c:81412
c:29261
c:69079
c:186184
c:12817
c:224114
c:84958
c:269049
c:269404
c:5208
c:233321
c:193244
c:178719
c:154693
c:269296
c:269336
c:15259
c:5233
c:73314
c:156296
c:268445
c:176864
c:141804
c:269937
c:221037
c:9385
c:183709
c:67716
c:216105
c:215653
c:228407
c:179100
c:247849
c:259768
c:177604
c:186803
c:52126
c:258747
c:34373
c:452

In [141]:
def fillzeros(x):
    #print(x)
    if np.isnan(x).all():
        x = np.zeros(4)
    return x

for i in range(1,224):
    df_unique_milestone.iloc[:,i] = df_unique_milestone.iloc[:,i].apply(fillzeros)

for i in range(2,224):
    df_unique_milestone.iloc[:,i] += df_unique_milestone.iloc[:,i-1] 
df_unique_milestone

milestone_object_id                          mle0  \
0                    c:12          [0.0, 0.0, 2.0, 0.0]   
1                    c:59          [0.0, 0.0, 0.0, 0.0]   
2                   c:314          [0.0, 0.0, 0.0, 0.0]   
4                   c:283          [0.0, 0.0, 0.0, 0.0]   
5                  c:6816          [0.0, 0.0, 0.0, 0.0]   
7                  c:5874          [0.0, 0.0, 0.0, 0.0]   
8                  c:2034          [0.0, 0.0, 0.0, 0.0]   
9                  c:5085          [0.0, 0.0, 0.0, 0.0]   
10                 c:1388          [0.0, 0.0, 0.0, 0.0]   
11                   c:75          [0.0, 0.0, 0.0, 0.0]   
12                 c:6947          [0.0, 0.0, 2.0, 0.0]   
20                 c:3515          [0.0, 0.0, 0.0, 0.0]   
22                 c:5411          [0.0, 0.0, 0.0, 0.0]   
23                 c:2391          [0.0, 0.0, 0.0, 0.0]   
24                 c:6501          [0.0, 0.0, 0.0, 0.0]   
25                 c:4068          [0.0, 0.0, 0.0, 0.0]   
26                 c:1972          [0.0, 0.0, 0.0, 0.0]   
27                 c:5149          [0.0, 0.0, 0.0, 0.0]   
29                 c:1298          [0.0, 0.0, 0.0, 0.0]   
31                   c:97          [0.0, 0.0, 0.0, 0.0]   
37                 c:6995          [0.0, 0.0, 3.0, 0.0]   
45                 c:4366          [0.0, 0.0, 0.0, 0.0]   
46                 c:7163          [0.0, 0.0, 0.0, 0.0]   
47                  c:183          [0.0, 0.0, 0.0, 0.0]   
48                 c:7199          [0.0, 0.0, 0.0, 0.0]   
50                 c:3692          [0.0, 0.0, 0.0, 0.0]   
51                 c:7127          [0.0, 0.0, 0.0, 0.0]   
53                 c:1600          [0.0, 0.0, 0.0, 0.0]   
54                  c:259          [0.0, 0.0, 0.0, 0.0]   
55                 c:5067          [0.0, 0.0, 0.0, 0.0]   
...                   ...                           ...   
22843            c:279562          [0.0, 0.0, 0.0, 0.0]   
22847            c:285256  [0.23, 0.2732, 0.442, 0.327]   
22849             c:84318          [0.0, 0.0, 0.0, 0.0]   
22850             c:25310          [0.0, 0.0, 0.0, 0.0]   
22855             c:37740          [0.0, 0.0, 0.0, 0.0]   
22856            c:224118          [0.0, 0.0, 0.0, 0.0]   
22857            c:285493          [0.0, 0.0, 0.0, 0.0]   
22858            c:224659          [0.0, 0.0, 0.0, 0.0]   
22860            c:241062          [0.0, 0.0, 0.0, 0.0]   
22861            c:284084          [0.0, 0.0, 0.0, 0.0]   
22866            c:189020          [0.0, 0.0, 0.0, 0.0]   
22870             c:10099          [0.0, 0.0, 0.0, 0.0]   
22871             c:71430          [0.0, 0.0, 0.0, 0.0]   
22877            c:242634          [0.0, 0.0, 0.0, 0.0]   
22889            c:223714          [0.0, 0.0, 0.0, 0.0]   
22890            c:158182          [0.0, 0.0, 0.0, 0.0]   
22894             c:36508          [0.0, 0.0, 0.0, 0.0]   
22898            c:177209          [0.0, 0.0, 0.0, 0.0]   
22899            c:104151          [0.0, 0.0, 0.0, 0.0]   
22900            c:284350          [0.0, 0.0, 0.0, 0.0]   
22901            c:229061          [0.0, 0.0, 0.0, 0.0]   
22907            c:157979          [0.0, 0.0, 0.0, 0.0]   
22911            c:166739          [0.0, 0.0, 0.0, 0.0]   
22913            c:189582          [0.0, 0.0, 0.0, 0.0]   
22914             c:63800          [0.0, 0.0, 0.0, 0.0]   
22915            c:285948          [0.0, 0.0, 0.0, 0.0]   
22916            c:270027          [0.0, 0.0, 0.0, 0.0]   
22918            c:285950   [0.0, 0.1779, 0.779, 0.221]   
22920             c:82091          [0.0, 0.0, 0.0, 0.0]   
22921             c:60389          [0.0, 0.0, 0.0, 0.0]   

                                          mle1  \
0                         [0.0, 0.0, 2.0, 0.0]   
1                         [0.0, 0.0, 0.0, 0.0]   
2                         [0.0, 0.0, 0.0, 0.0]   
4                         [0.0, 0.0, 0.0, 0.0]   
5                         [0.0, 0.0, 0.0, 0.0]   
7                         [0.0, 0.0, 0.0, 0.0] 

# Merge product

In [138]:

allcolumns = ["product_object_id"]
for i in range(209):
    allcolumns += ['pro' + str(i)]

df_unique_product = pd.DataFrame(columns=allcolumns)
df_unique_product ["product_object_id"] = df_product.drop_duplicates("product_object_id")["product_object_id"]
df_unique_product.info()

def mergeProduct(x):
    row = []
    df_row = df_product.loc[df_product["product_object_id"] == x["product_object_id"]]
    #print(x["product_object_id"])
    max_time = df_row["product_time_since_founded"].max()
    for i in range(int(max_time/window_size)+1):

        item = df_row.loc[(df_row["product_time_since_founded"] >= i * window_size)
                          & (df_row["product_time_since_founded"] < (i+1) * window_size)]
        row.append(item.iloc[:,2:9].sum().values)
    for i in range(int(max_time/window_size)+1, 209):
        row.append(np.nan)
    return list(row)

df_unique_product.iloc[:,1:210] = df_unique_product.apply(mergeProduct, axis=1,result_type='expand').values


<class 'pandas.core.frame.DataFrame'>
Int64Index: 8907 entries, 0 to 22081
Columns: 210 entries, product_object_id to pro208
dtypes: object(210)
memory usage: 14.3+ MB


In [139]:
def fillzeros(x):
    #print(x)
    if np.isnan(x).all():
        x = np.zeros(7)
    return x

for i in range(1,210):
    df_unique_product.iloc[:,i] = df_unique_product.iloc[:,i].apply(fillzeros)
    if i >=2:
        df_unique_product.iloc[:,i] += df_unique_product.iloc[:,i-1]  

df_unique_product

product_object_id                   pro0  \
0                   c:1  [0, 0, 0, 0, 0, 1, 0]   
1                  c:16  [0, 0, 0, 0, 0, 0, 0]   
2                c:1585  [0, 0, 0, 0, 0, 0, 0]   
3               c:14171  [0, 0, 0, 0, 0, 1, 0]   
4               c:14180  [0, 0, 0, 0, 0, 3, 0]   
7               c:14184  [0, 0, 0, 0, 0, 1, 0]   
8               c:14187  [0, 0, 0, 0, 0, 1, 0]   
9                c:6268  [0, 0, 0, 0, 1, 0, 0]   
10              c:14198  [0, 0, 0, 0, 0, 2, 0]   
12              c:14201  [0, 1, 0, 0, 0, 1, 0]   
14              c:14202  [0, 0, 0, 0, 0, 1, 0]   
16              c:14209  [0, 0, 0, 0, 0, 2, 0]   
18              c:14215  [0, 0, 0, 0, 0, 0, 0]   
19              c:14216  [0, 0, 0, 0, 0, 2, 0]   
21              c:14218  [0, 0, 0, 0, 0, 1, 0]   
22              c:14219  [0, 0, 0, 0, 0, 3, 0]   
25               c:2972  [0, 0, 0, 0, 0, 1, 0]   
27              c:14221  [0, 0, 0, 0, 0, 0, 0]   
28              c:14227  [0, 0, 0, 0, 0, 1, 0]   
29               c:1170  [0, 0, 0, 0, 1, 0, 0]   
30              c:14228  [0, 0, 0, 0, 0, 3, 0]   
33               c:4602  [0, 0, 0, 0, 0, 3, 0]   
36              c:14244  [0, 0, 0, 0, 0, 3, 0]   
39              c:14247  [0, 0, 0, 0, 0, 3, 0]   
42              c:14251  [0, 0, 0, 0, 0, 1, 0]   
43              c:14253  [0, 0, 0, 0, 0, 3, 0]   
44               c:1172  [0, 0, 0, 0, 0, 0, 0]   
47              c:14259  [0, 0, 0, 0, 0, 1, 0]   
48              c:14269  [0, 0, 0, 0, 0, 3, 0]   
51              c:14276  [0, 0, 0, 0, 0, 1, 0]   
...                 ...                    ...   
22023           c:14027  [0, 0, 0, 0, 0, 1, 0]   
22027           c:14036  [0, 0, 0, 0, 0, 2, 0]   
22029           c:14041  [0, 0, 0, 0, 0, 1, 0]   
22030           c:14042  [0, 0, 0, 0, 0, 1, 0]   
22033           c:14057  [0, 0, 0, 0, 0, 1, 0]   
22036           c:14059  [0, 0, 0, 0, 0, 1, 0]   
22037           c:14029  [0, 0, 0, 0, 0, 3, 0]   
22040           c:14063  [0, 0, 0, 0, 0, 1, 0]   
22041           c:14065  [0, 0, 0, 0, 0, 0, 0]   
22042           c:14077  [0, 0, 0, 0, 0, 5, 0]   
22048           c:14083  [0, 0, 0, 0, 0, 1, 0]   
22049           c:14087  [0, 0, 0, 0, 0, 1, 0]   
22050           c:14091  [0, 0, 0, 0, 0, 1, 0]   
22051           c:14092  [0, 0, 0, 0, 0, 2, 0]   
22053           c:14095  [0, 0, 0, 0, 0, 2, 0]   
22055           c:14101  [0, 0, 0, 0, 1, 0, 0]   
22060           c:14108  [0, 0, 0, 0, 0, 1, 0]   
22061           c:14115  [0, 0, 0, 0, 0, 1, 0]   
22062           c:14119  [0, 0, 0, 0, 0, 2, 0]   
22065           c:14122  [0, 0, 0, 0, 0, 1, 0]   
22066           c:14123  [0, 0, 0, 0, 0, 1, 0]   
22067            c:1164  [0, 0, 0, 0, 0, 0, 0]   
22068           c:14132  [0, 1, 0, 0, 0, 0, 0]   
22069           c:14134  [0, 0, 0, 0, 0, 1, 0]   
22070           c:14140  [0, 0, 0, 0, 0, 3, 0]   
22073           c:14141  [0, 0, 0, 0, 0, 0, 0]   
22074           c:14144  [0, 0, 0, 0, 0, 1, 0]   
22078           c:14155  [0, 0, 0, 0, 0, 1, 0]   
22080           c:14156  [0, 0, 0, 0, 0, 1, 0]   
22081           c:14164  [0, 0, 0, 0, 0, 6, 0]   

                                      pro1  \
0                    [0, 0, 0, 0, 1, 1, 0]   
1                    [0, 0, 0, 0, 0, 0, 0]   
2                    [0, 0, 0, 0, 0, 0, 0]   
3      [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0]   
4      [0.0, 0.0, 0.0, 0.0, 0.0, 3.0, 0.0]   
7      [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0]   
8      [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0]   
9      [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0]   
10     [0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0]   
12                   [0, 1, 0, 0, 0, 1, 0]   
14                   [0, 0, 0, 0, 0, 1, 0]   
16     [0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0]   
18                   [0, 0, 0, 0, 0, 0, 0]   
19     [0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0]   
21     [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0]   
22     [0.0, 0.0, 0.0, 0.0, 0.0, 3.0, 0.0]   
25     [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0]   
27                   [0, 0, 0, 0, 0, 0, 0]   
28                   [0, 0, 0, 

# Merge ipo

In [620]:
allcolumns = ["ipo_object_id"]
for i in range(1,227):
    allcolumns += ['ipo_window' + str(i)]
df_unique_ipo = pd.DataFrame(columns=allcolumns)
df_unique_ipo ["ipo_object_id"] = df_ipo.drop_duplicates("object_id")["object_id"]

def ipoY(x):
    row = []
    df_row = df_ipo.loc[df_ipo["object_id"] == x["ipo_object_id"]]
    #print(x["ipo_object_id"])
    #print(df_row)
    max_time = df_row["ipo_time_since_founded"].max()
    for i in range(1, int(max_time/window_size)+1):
        if(df_row["ipo_time_since_founded"] >= i * window_size).all()&(df_row["ipo_time_since_founded"] < (i+1) * window_size).all():
            row.append(1)
        else:
            row.append(0)
    for i in range(int(max_time/window_size)+1, 227):
        row.append(0)
    return list(row)
        
df_unique_ipo.iloc[:,1:227]  = df_unique_ipo.apply(ipoY,axis=1,result_type='expand').values

In [621]:
df_unique_ipo

ipo_object_id ipo_window1 ipo_window2 ipo_window3 ipo_window4 ipo_window5  \
0          c:4495           0           0           0           0           0   
1        c:144059           0           0           0           0           0   
2           c:475           0           0           0           0           0   
3         c:10614           0           0           0           0           0   
4        c:164413           1           0           0           0           0   
5        c:145411           1           0           0           0           0   
6        c:281988           0           0           1           0           0   
7        c:235945           0           0           1           0           0   
8         c:48759           0           0           0           1           0   
9         c:22130           0           0           0           1           0   
10       c:245010           0           0           0           0           1   
11       c:258641           0           0           0           0           1   
12       c:265792           0           0           0           0           1   
13         c:1368           0           0           0           0           1   
14        c:37881           0           0           0           0           0   
15        c:11391           0           0           0           0           0   
16        c:24982           0           0           0           0           0   
17          c:108           0           0           0           0           0   
18        c:40482           0           0           0           0           0   
19       c:241173           0           0           0           0           0   
20        c:46007           0           0           0           0           0   
21       c:258957           0           0           0           0           0   
22        c:37431           0           0           0           0           0   
23        c:37940           0           0           0           0           0   
24         c:1448           0           0           0           0           0   
25        c:15609           0           0           0           0           0   
26        c:43666           0           0           0           0           0   
27        c:38270           0           0           0           0           0   
28         c:1249           0           0           0           0           0   
29         c:1812           0           0           0           0           0   
..            ...         ...         ...         ...         ...         ...   
675         c:355           0           0           0           0           0   
676       c:64802           0           0           0           0           0   
677       c:39278           0           0           0           0           0   
678       c:34406           0           0           0           0           0   
679       c:58207           0           0           0           0           0   
680       c:37380           0           0           0           0           0   
681       c:39330           0           0           0           0           0   
682        c:4304           0           0           0           0           0   
683       c:30927           0           0           0           0           0   
684      c:223939           0           0           0           0           0   
685        c:1915           0           0           0           0           0   
686         c:342           0           0           0           0           0   
687       c:20016           0           0           0           0           0   
688      c:274050           0           0           0           0           0   
689        c:7576           0           0           0           0           0   
690       c:34181           0           0           0           0           0   
691         c:541           0           0           0           0           0   
692        c:3658           0      

# Merge acquired 

In [627]:
allcolumns = ["acquired_object_id"]
for i in range(1,227):
    allcolumns += ['acquired_window' + str(i)]
df_unique_acquired = pd.DataFrame(columns=allcolumns)
df_unique_acquired ["acquired_object_id"] = df_acquired.drop_duplicates("acquired_object_id")["acquired_object_id"]

def acquiredY(x):
    row = []
    df_row = df_acquired.loc[df_acquired["acquired_object_id"] == x["acquired_object_id"]]
    #print(x["ipo_object_id"])
    #print(df_row)
    max_time = df_row["acquired_time_since_founded"].max()
    for i in range(1, int(max_time/window_size)+1):
        if(df_row["acquired_time_since_founded"] >= i * window_size).any()&(df_row["acquired_time_since_founded"] < (i+1) * window_size).any():
            row.append(1)
        else:
            row.append(0)
    for i in range(int(max_time/window_size)+1, 227):
        row.append(0)
    return list(row)
        
df_unique_acquired.iloc[:,1:227]  = df_unique_acquired.apply(acquiredY,axis=1,result_type='expand').values

# Merge output

In [77]:
df = df_unique_funding.iloc[:,[0]].join(df_unique_funding.iloc[:,187:-1])
allcolumns=[]
for i in range(185,227):
    allcolumns += ['funding_window' + str(i)]
df_append = pd.DataFrame(index=df.index, columns=allcolumns)
df = df.join(df_append)
df.fillna(0, inplace=True)

df_output = pd.merge(df, df_unique_ipo, how='left',left_on='funding_object_id', right_on='ipo_object_id')
display(df_output.columns)
df_output = pd.merge(df_output, df_unique_acquired, how='left',left_on='funding_object_id', right_on='acquired_object_id')
display(df_output.columns)

df_output.drop(columns=["ipo_object_id","acquired_object_id"],inplace=True)
df_output.fillna(0,inplace=True)


df_output.iloc[:,1:] = df_output.iloc[:,1:].astype('bool')
for i in range(1,226):
    if i==1:
        print(df_output.iloc[0,i])
        print(df_output.iloc[0,i+226])
        print(df_output.iloc[0,i+226*2])
       
    df_output.iloc[:,i] = df_output.iloc[:,i] | df_output.iloc[:,i+225] | df_output.iloc[:,i+226+225] 



df_output = df_output.iloc[:,:227]

In [78]:
df_output

funding_object_id  funding_window1  funding_window2  funding_window3  \
0              c:144040                0                0                0   
1               c:18038                0                1                0   
2              c:161452                0                0                0   
3              c:161453                0                0                0   
4              c:161480                0                0                0   
5              c:264245                0                1                0   
6               c:18202                0                1                0   
7               c:51578                0                1                0   
8              c:161699                0                0                0   
9              c:161944                0                0                0   
10               c:4299                0                0                0   
11             c:263989                0                0                0   
12              c:68549                0                0                0   
13              c:68486                0                0                0   
14              c:68442                0                0                0   
15             c:162067                0                0                0   
16              c:18701                0                0                0   
17              c:18741                0                0                0   
18             c:264553                0                0                0   
19              c:68329                0                0                0   
20              c:45196                0                0                0   
21              c:69063                0                0                0   
22             c:265497                0                0                0   
23             c:161240                0                0                0   
24             c:265463                0                0                0   
25              c:64996                0                0                0   
26              c:17758                0                0                0   
27             c:265370                0                0                0   
28              c:69596                0                0                0   
29             c:265241                0                0                0   
...                 ...              ...              ...              ...   
16748          c:261056                0                0                0   
16749          c:266200                0                0                0   
16750          c:145945                0                0                0   
16751           c:59556                0                0                0   
16752          c:220572                0                0                0   
16753          c:243852                0                0                0   
16754           c:69136                0                0                0   
16755          c:212776                0                0                0   
16756          c:244910                0                0                0   
16757           c:16243                0                0                0   
16758          c:277196                0                0                0   
16759            c:6713                0                0                0   
16760          c:245323                0                0                0   
16761           c:35691                0                0                0   
16762          c:219131                0                0                0   
16763          c:267819                0                0                0   
16764          c:177075                0                0                0   
16765          c:144811                0                0                0   
16766           c:36848                0                0                0   
16767          c:164565     

In [144]:
df_unique_acquiring.to_pickle('./merge_pkl/acquiring.pkl')
df_unique_product.to_pickle('./merge_pkl/product.pkl')
df_unique_milestone.to_pickle('./merge_pkl/milestone.pkl')
df_unique_funding.to_pickle('./merge_pkl/funding.pkl')


# Import merge csv

In [ ]:
df_unique_funding.to_csv('./merge_csv/funding.csv')

df_unique_acquiring.to_csv('./merge_csv/acquiring.csv')
df_unique_product.to_csv('./merge_csv/product.csv')
df_unique_milestone.to_csv('./merge_csv/milestone.csv')

df_unique_ipo.to_csv('./merge_csv/ipo.csv')
df_unique_acquired.to_csv('./merge_csv/acquired.csv')


In [79]:
df_output.to_csv('./merge_csv/outputY.csv')

In [93]:

df_unique_funding = pd.read_csv('./merge_csv/funding.csv')
df_unique_acquiring = pd.read_csv('./merge_csv/acquiring.csv')
df_unique_product = pd.read_csv('./merge_csv/product.csv')
df_unique_milestone = pd.read_csv('./merge_csv/milestone.csv')

df_unique_ipo = pd.read_csv('./merge_csv/ipo.csv')
df_unique_acquired = pd.read_csv('./merge_csv/acquired.csv')

df_unique_funding = df_unique_funding.drop(columns="Unnamed: 0")
df_unique_acquiring = df_unique_acquiring.drop(columns="Unnamed: 0")
df_unique_product = df_unique_product.drop(columns="Unnamed: 0")
df_unique_milestone = df_unique_milestone.drop(columns="Unnamed: 0")
df_unique_ipo = df_unique_ipo.drop(columns="Unnamed: 0")
df_unique_acquired = df_unique_acquired.drop(columns="Unnamed: 0")

In [147]:
df_output.iloc[0,3].dtype

dtype('int64')

In [148]:
df_output.to_pickle('./merge_pkl/outputY.pkl')

In [3]:
import pandas as pd
df_output = pd.read_pickle('./merge_pkl/outputY.pkl')

In [9]:
import numpy as np
Y = df_output.values[:, 1:]
Y.shape
np.save("Y", Y)

In [10]:
Y = np.load("Y.npy")
Y.shape

(16778, 226)